In [1]:
# procedure for calculating hydraulic confinement along a pressure tunnel 
# completed procedure will in the form of a design report
#   safety factor against hydraulic confinement calculated at stationed points along tunnel alignment
#   calculation determines the minimum dstance from the stationed point to the terrain surface 

# project name: 'Snow Mountain 2.0 PSP' 

In [2]:
# ToDo
#   DONE need to read in 'slope' and get slope values for all buffer grid points 'MIN'
#   DONE Nam Ang headrace tunnel alignment and DTM
#   DONE add calculation for hydraulic confinement safety factor (SF)
#   DONE add results plot for hydraulic confinement safety factor
#   put common functions (e.g. setup, data format conversions) into a separate module/API
#   DONE use Nam Ang HEP data for initial testing and demo
#   provide full desgin criteria text in Jupyter Notebook design report
#   DONE add check plot with alignment, station points, buffer points
#   DONE add check plot with MIN buffer grid points
#   refactor code

In [3]:
# import required python libraires
import numpy as np
from numpy import *
import pandas as pd
import geopandas as gpd
import shapely as sp
#import matplotlib.pylab as pylab  #matplotlib not currently used
#import matplotlib.pyplot as plt
#%matplotlib inline

# testing
#import random
# check pd and gpd version
#print(pd.__version__)
#print(gpd.__version__)

In [4]:
# python setup for qgis processing
import sys, os
from qgis.core import QgsApplication
from PyQt4.QtGui import QApplication
app = QApplication([], True)  #True -> window display enabled
QgsApplication.setPrefixPath("/usr", True)
QgsApplication.initQgis()
sys.path.append('/usr/share/qgis/python/plugins')  #export PYTHONPATH not needed in start script
from processing.core.Processing import Processing
Processing.initialize() 
import processing
#from processing.tools import *  #not needed currently

In [5]:
# set up plotly in 'offline' mode                            #ToDo JK: this should be cleaned up and documented
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot,iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
print (__version__) # requires version >= 1.9.0

# collect all plotly setups here
import plotly.offline as plotly
from plotly.graph_objs import *

2.2.1


In [6]:
# import DSS modules
#import geospatial as geo

In [7]:
# set wd for this procedure and project 
os.chdir("/home/kaelin_joseph/DSS.HydraulicConfinement/")

In [8]:
# set maximum number of rows to display from a pandas data frame
#pd.set_option('display.max_rows', 3000)
pd.set_option('display.max_rows', 30000)

In [9]:
# define required input files
# for Snowy Mountain 2.0 PSP, alignment data will be defined in Jupyter Notebook, to better document alternatives studied
##Alignment = "data/in/SnowMountains2.WaterwaysAlignment.r2.csv"  #D/S PH, vertical shaft waterways alignment
DTM = "data/in/SnowyMountainsTopogRaster.tif"  #DEM with surface topography
#   Alignment contains fields "Point","Type","Station","Northing","Easting","Elevation"
#   check Alignment data: no spaces between comma-separated fields
#   check Alignment data: no trailing blank lines, no duplicate lines
DTM_slope='data/in/SnowyMountainsSlopeRaster.tif'  #DEM containing slope angle as attribute

In [10]:
# #JV r2 (vertical shaft)
# alignment = {
#     'Station':["18+500.0","19+400.0","19+650.0","19+700.0","20+150.0"],
#     'Northing':[6038594.951,6038611.442,6038458.908,6038422.009,6038135.211],
#     'Easting':[631021.964,630122.473,629930.936,629897.196,629563.649],
#     'Elevation':[1078.121,1076.866,1076.518,438.769,421.364]
#     }

In [11]:
# #JV JV1 (vertical shaft)
# alignment = { 
#     'Station':["16+956", "19+348.7", "19+512.6", "19+512.6", "19+602", "19+608"],
#     'Northing':[6038616.024, 6038680.380, 6038684.787, 6038684.787, 6038687.191, 6038687.358],
#     'Easting':[632522.964, 630130.630, 629966.831, 629966.831, 629877.463, 629871.245],
#     'Elevation':[1101.00, 1097.51, 1081.12, 448.94, 440.00, 432.00]
#     }

In [12]:
#JV JV1 (vertical shaft)
alignment = { 
    'Station':[16956, 19348.7, 19512.6, 19512.6, 19602, 19608],
    'Northing':[6038616.024, 6038680.380, 6038684.787, 6038684.787, 6038687.191, 6038687.358],
    'Easting':[632522.964, 630130.630, 629967.831, 629966.831, 629877.463, 629871.245],
    'Elevation':[1101.00, 1097.51, 1081.12, 448.94, 440.00, 432.00]
    }

In [13]:
# define required input data

# mapping
crs = {'init': 'epsg:32755'}  #define crs for project Snowy Mountains 2
grass_region = "619000,656000,6029000,6043000"  #map region E1,E2,N1,N2 Snowy Mountains 2

# resolution for analysis
#grass_station_dist = 20  #use for high resolution
grass_station_dist = 50  #use for low resolution
c = 0.5  #ring buffer radius = c*h  (h=overburden)
#res = 3.0  #use for high resolution
res = 25.0  #use for low resolution

# rock properties
density_rock = 27.0  #kN/m3

# hydraulic properties
max_static_water_level = 1228.7 + 80 #MASL, include upsurge

####
#start_station = alignment['Station'][0]  ####
start_station = 0.0
print(start_station)  ####

16956


In [14]:
alignment_df = pd.DataFrame(alignment)
alignment_df = alignment_df[['Station','Northing','Easting','Elevation']]  #for checking

In [15]:
# define temporary data
Alignment_shp ='tmp/SnowyMtn2Alignment.shp'  #alignment shp from Alignment
Alignment_grass_csv = 'tmp/SnowyMtn2AlignmentGrass.csv'  #alignment csv fixed for grass
Alignment_line_shp = "tmp/SnowyMtn2AlignmentLine.shp"  #intermediate data
Alignment_stationed_shp = "tmp/SnowyMtn2AlignmentStationed.shp"  #alignment shp containing station points
Alignment_dtm_csv = "tmp/SnowyMtn2AlignmentDTM.csv"  #alignment including terrain elevations at station points
Buffer_shp = "tmp/SnowyMtn2Buffer.shp"  #buffer shp containing ring grid points at a particular station point
Buffer_all_csv = "tmp/SnowyMtn2BufferAll.csv"  # all station point ring buffers written to csv
Buffer_all_shp = "tmp/SnowyMtn2BufferFinal.shp"
Buffer_dtm_csv = "tmp/SnowyMtn2BufferDTM.csv"
Buffer_slope_csv = "tmp/SnowyMtn2BufferSlope.csv"

In [16]:
# define output files


In [17]:
# for Snowy Mountain 2.0 PSP, data will be defined in Jupyter Notebook, to better document alternatives studied
# # create alignment_df (dataframe) from Alignment csv                     #ToDo JK: make into csv -> df function
# alignment_df = pd.read_csv(Alignment)

# # delete row if only NA are present in row
# alignment_df = alignment_df.dropna(how = "all")
# # round alignment_df to three decimals
# alignment_df = alignment_df.round(decimals=3)

In [18]:
alignment_df

Station     Northing     Easting  Elevation
0  16956.0  6038616.024  632522.964    1101.00
1  19348.7  6038680.380  630130.630    1097.51
2  19512.6  6038684.787  629967.831    1081.12
3  19512.6  6038684.787  629966.831     448.94
4  19602.0  6038687.191  629877.463     440.00
5  19608.0  6038687.358  629871.245     432.00

In [19]:
# create stationed alignment as Alignment_stationed_shp                 #ToDo JK: make into stationing function
# from points in alignment_df
#   required grass input data: x, y coordinates at each alignment point
#   grass input for function v.in.line 1) must have x first and y second; 2) no header 
#   grass output: x, y coordinates at each station point along alignment
alignment_df_grass = alignment_df.loc[:,["Easting", "Northing"]]  #x first and y second
# write Alignment_grass_csv
alignment_df_grass.to_csv(Alignment_grass_csv, header=False, index=False)  #no header

# points to line, write output to Alignment_line_shp
processing.runalg("grass7:v.in.lines",Alignment_grass_csv,",",False,
                  grass_region,0,Alignment_line_shp)  #no spaces between commas

# line to station points, ouput segmented polyline to Alignment_stationed_shp
processing.runalg("grass7:v.to.points",Alignment_line_shp,grass_station_dist,1,True,
                  grass_region,-1,0.0001,0,Alignment_stationed_shp)  #no spaces between commas

{'output': 'tmp/SnowyMtn2AlignmentStationed.shp'}

In [20]:
# create alignment_stationed_df from Alignment_stationed_shp            #ToDo JK: make into shp -> df function
#   required output data: x_align, y_align at each station point
alignment_stationed_df = gpd.read_file(Alignment_stationed_shp)

# create columns for x_align, y_align, then delete columns cat_ and geometry
alignment_stationed_df["x_align"] = alignment_stationed_df.geometry.x
alignment_stationed_df["y_align"] = alignment_stationed_df.geometry.y
alignment_stationed_df = alignment_stationed_df.drop(columns =["cat_", "geometry"])

In [21]:
alignment_stationed_df

x_align       y_align
0   632522.964000  6.038616e+06
1   632473.123708  6.038617e+06
2   632423.283417  6.038619e+06
3   632373.443125  6.038620e+06
4   632323.602833  6.038621e+06
5   632273.762542  6.038623e+06
6   632223.922250  6.038624e+06
7   632174.081958  6.038625e+06
8   632124.241667  6.038627e+06
9   632074.401375  6.038628e+06
10  632024.561083  6.038629e+06
11  631974.720792  6.038631e+06
12  631924.880500  6.038632e+06
13  631875.040208  6.038633e+06
14  631825.199917  6.038635e+06
15  631775.359625  6.038636e+06
16  631725.519333  6.038637e+06
17  631675.679042  6.038639e+06
18  631625.838750  6.038640e+06
19  631575.998458  6.038641e+06
20  631526.158167  6.038643e+06
21  631476.317875  6.038644e+06
22  631426.477583  6.038646e+06
23  631376.637292  6.038647e+06
24  631326.797000  6.038648e+06
25  631276.956708  6.038650e+06
26  631227.116417  6.038651e+06
27  631177.276125  6.038652e+06
28  631127.435833  6.038654e+06
29  631077.595542  6.038655e+06
30  631027.755250  6.038656e+06
31  630977.914958  6.038658e+06
32  630928.074667  6.038659e+06
33  630878.234375  6.038660e+06
34  630828.394083  6.038662e+06
35  630778.553792  6.038663e+06
36  630728.713500  6.038664e+06
37  630678.873208  6.038666e+06
38  630629.032917  6.038667e+06
39  630579.192625  6.038668e+06
40  630529.352333  6.038670e+06
41  630479.512042  6.038671e+06
42  630429.671750  6.038672e+06
43  630379.831458  6.038674e+06
44  630329.991167  6.038675e+06
45  630280.150875  6.038676e+06
46  630230.310583  6.038678e+06
47  630180.470292  6.038679e+06
48  630130.630000  6.038680e+06
49  630089.930250  6.038681e+06
50  630049.230500  6.038683e+06
51  630008.530750  6.038684e+06
52  629967.831000  6.038685e+06
53  629966.831000  6.038685e+06
54  629922.147000  6.038686e+06
55  629877.463000  6.038687e+06
56  629871.245000  6.038687e+06

In [22]:
# add required fields to alignment_stationed_df

# add "id" 
alignment_stationed_df["id_point"] = alignment_stationed_df.index

# add "distance_stat" referencing length between point n and point n+1
#   is this what is intended??                                                                       ToDo: JK
alignment_stationed_df["distance_stat"] = np.nan
for n in range(0, len(alignment_stationed_df)-1):
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")] = (
        ((alignment_stationed_df.iloc[n +1]["x_align"] - alignment_stationed_df.iloc[n]["x_align"])**2
        +(alignment_stationed_df.iloc[n +1]["y_align"] - alignment_stationed_df.iloc[n]["y_align"])**2 )**(0.5) )

# add "distance_stat_sum"
alignment_stationed_df["distance_stat_sum"] = np.nan
alignment_stationed_df.iloc[0, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = start_station  ####
####for n in range(1, len(alignment_stationed_df) -1):
for n in range(1, len(alignment_stationed_df)):  #refactor !!!
    ####distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n +1))), 
    ####                    "distance_stat"] )
    distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n))), 
                        "distance_stat"] )
    distances = distance.tolist()
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = (
                                                                               sum(distances) +start_station)
    
#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum
0   632522.964000  6.038616e+06         0      49.858322       16956.000000
1   632473.123708  6.038617e+06         1      49.858322       17005.858322
2   632423.283417  6.038619e+06         2      49.858322       17055.716644
3   632373.443125  6.038620e+06         3      49.858322       17105.574966
4   632323.602833  6.038621e+06         4      49.858322       17155.433288
5   632273.762542  6.038623e+06         5      49.858322       17205.291611
6   632223.922250  6.038624e+06         6      49.858322       17255.149933
7   632174.081958  6.038625e+06         7      49.858322       17305.008255
8   632124.241667  6.038627e+06         8      49.858322       17354.866577
9   632074.401375  6.038628e+06         9      49.858322       17404.724899
10  632024.561083  6.038629e+06        10      49.858322       17454.583221
11  631974.720792  6.038631e+06        11      49.858322       17504.441543
12  631924.880500  6.038632e+06        12      49.858322       17554.299865
13  631875.040208  6.038633e+06        13      49.858322       17604.158187
14  631825.199917  6.038635e+06        14      49.858322       17654.016510
15  631775.359625  6.038636e+06        15      49.858322       17703.874832
16  631725.519333  6.038637e+06        16      49.858322       17753.733154
17  631675.679042  6.038639e+06        17      49.858322       17803.591476
18  631625.838750  6.038640e+06        18      49.858322       17853.449798
19  631575.998458  6.038641e+06        19      49.858322       17903.308120
20  631526.158167  6.038643e+06        20      49.858322       17953.166442
21  631476.317875  6.038644e+06        21      49.858322       18003.024764
22  631426.477583  6.038646e+06        22      49.858322       18052.883086
23  631376.637292  6.038647e+06        23      49.858322       18102.741409
24  631326.797000  6.038648e+06        24      49.858322       18152.599731
25  631276.956708  6.038650e+06        25      49.858322       18202.458053
26  631227.116417  6.038651e+06        26      49.858322       18252.316375
27  631177.276125  6.038652e+06        27      49.858322       18302.174697
28  631127.435833  6.038654e+06        28      49.858322       18352.033019
29  631077.595542  6.038655e+06        29      49.858322       18401.891341
30  631027.755250  6.038656e+06        30      49.858322       18451.749663
31  630977.914958  6.038658e+06        31      49.858322       18501.607986
32  630928.074667  6.038659e+06        32      49.858322       18551.466308
33  630878.234375  6.038660e+06        33      49.858322       18601.324630
34  630828.394083  6.038662e+06        34      49.858322       18651.182952
35  630778.553792  6.038663e+06        35      49.858322       18701.041274
36  630728.713500  6.038664e+06        36      49.858322       18750.899596
37  630678.873208  6.038666e+06        37      49.858322       18800.757918
38  630629.032917  6.038667e+06        38      49.858322       18850.616240
39  630579.192625  6.038668e+06        39      49.858322       18900.474562
40  630529.352333  6.038670e+06        40      49.858322       18950.332885
41  630479.512042  6.038671e+06        41      49.858322       19000.191207
42  630429.671750  6.038672e+06        42      49.858322       19050.049529
43  630379.831458  6.038674e+06        43      49.858322       19099.907851
44  630329.991167  6.038675e+06        44      49.858322       19149.766173
45  630280.150875  6.038676e+06        45      49.858322       19199.624495
46  630230.310583  6.038678e+06        46      49.858322       19249.482817
47  630180.470292  6.038679e+06        47      49.858322       19299.341139
48  630130.630000  6.038680e+06        48      40.714660       19349.199461
49  630089.930250  6.038681e+06        49      40.714660       19389.914121
50  630049.230500  6.038683e+06        50      40.714660       19430.628781
51  630008.530750  6.038684e+06        51      40.714660  

In [23]:
# add required field "distance_intermed_align" to alignment_df
alignment_df["distance_intermed_align"] = np.nan

for n in range(0, len(alignment_df) -1):
    alignment_df.iloc[n, alignment_df.columns.get_loc("distance_intermed_align")] = (
        ((alignment_df.iloc[n +1]["Easting"]-alignment_df.iloc[n]["Easting"])**2 
             +(alignment_df.iloc[n +1]["Northing"]-alignment_df.iloc[n]["Northing"])**2 )**(0.5) )
    
#alignment_df.head()
alignment_df

Station     Northing     Easting  Elevation  distance_intermed_align
0  16956.0  6038616.024  632522.964    1101.00              2393.199461
1  19348.7  6038680.380  630130.630    1097.51               162.858638
2  19512.6  6038684.787  629967.831    1081.12                 1.000000
3  19512.6  6038684.787  629966.831     448.94                89.400328
4  19602.0  6038687.191  629877.463     440.00                 6.220242
5  19608.0  6038687.358  629871.245     432.00                      NaN

In [24]:
# join alignment_df to alignment_stationed_df
alignment_stationed_df = pd.merge(left= alignment_stationed_df, right = alignment_df, 
                 left_on = ["x_align","y_align"], 
                 right_on = ["Easting","Northing"], how = "left")

# clean up alignment_stationed_df
try:
    alignment_stationed_df = (
        alignment_stationed_df.drop(columns =["Point", "Type", "Northing", "Easting"]) )
except:
    pass

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   632522.964000  6.038616e+06         0      49.858322       16956.000000   
1   632473.123708  6.038617e+06         1      49.858322       17005.858322   
2   632423.283417  6.038619e+06         2      49.858322       17055.716644   
3   632373.443125  6.038620e+06         3      49.858322       17105.574966   
4   632323.602833  6.038621e+06         4      49.858322       17155.433288   
5   632273.762542  6.038623e+06         5      49.858322       17205.291611   
6   632223.922250  6.038624e+06         6      49.858322       17255.149933   
7   632174.081958  6.038625e+06         7      49.858322       17305.008255   
8   632124.241667  6.038627e+06         8      49.858322       17354.866577   
9   632074.401375  6.038628e+06         9      49.858322       17404.724899   
10  632024.561083  6.038629e+06        10      49.858322       17454.583221   
11  631974.720792  6.038631e+06        11      49.858322       17504.441543   
12  631924.880500  6.038632e+06        12      49.858322       17554.299865   
13  631875.040208  6.038633e+06        13      49.858322       17604.158187   
14  631825.199917  6.038635e+06        14      49.858322       17654.016510   
15  631775.359625  6.038636e+06        15      49.858322       17703.874832   
16  631725.519333  6.038637e+06        16      49.858322       17753.733154   
17  631675.679042  6.038639e+06        17      49.858322       17803.591476   
18  631625.838750  6.038640e+06        18      49.858322       17853.449798   
19  631575.998458  6.038641e+06        19      49.858322       17903.308120   
20  631526.158167  6.038643e+06        20      49.858322       17953.166442   
21  631476.317875  6.038644e+06        21      49.858322       18003.024764   
22  631426.477583  6.038646e+06        22      49.858322       18052.883086   
23  631376.637292  6.038647e+06        23      49.858322       18102.741409   
24  631326.797000  6.038648e+06        24      49.858322       18152.599731   
25  631276.956708  6.038650e+06        25      49.858322       18202.458053   
26  631227.116417  6.038651e+06        26      49.858322       18252.316375   
27  631177.276125  6.038652e+06        27      49.858322       18302.174697   
28  631127.435833  6.038654e+06        28      49.858322       18352.033019   
29  631077.595542  6.038655e+06        29      49.858322       18401.891341   
30  631027.755250  6.038656e+06        30      49.858322       18451.749663   
31  630977.914958  6.038658e+06        31      49.858322       18501.607986   
32  630928.074667  6.038659e+06        32      49.858322       18551.466308   
33  630878.234375  6.038660e+06        33      49.858322       18601.324630   
34  630828.394083  6.038662e+06        34      49.858322       18651.182952   
35  630778.553792  6.038663e+06        35      49.858322       18701.041274   
36  630728.713500  6.038664e+06        36      49.858322       18750.899596   
37  630678.873208  6.038666e+06        37      49.858322       18800.757918   
38  630629.032917  6.038667e+06        38      49.858322       18850.616240   
39  630579.192625  6.038668e+06        39      49.858322       18900.474562   
40  630529.352333  6.038670e+06        40      49.858322       18950.332885   
41  630479.512042  6.038671e+06        41      49.858322       19000.191207   
42  630429.671750  6.038672e+06        42      49.858322       19050.049529   
43  630379.831458  6.038674e+06        43      49.858322       19099.907851   
44  630329.991167  6.038675e+06        44      49.858322       19149.766173   
45  630280.150875  6.038676e+06        45      49.858322       19199.624495   
46  630230.310583  6.038678e+06        46      49.858322       19249.482817   
47  630180.470292  6.038679e+06        47      49.858322       19299.341139   
48  630130.630000  6.038680e+06        48      40.714660       19349.199461   
49  630089.930250  6.038681e+06        49      40.714660    

In [25]:
# get id_points for alignment points in alignment_stationed_df 
#   select points where Elevation of point not NaN
id_points_align =  (
    alignment_stationed_df.loc[(alignment_stationed_df.Elevation.isin(alignment_df["Elevation"])), "id_point"] )
id_points_align= id_points_align.tolist()
id_points_align                                                                         

[0, 48, 52, 53, 55, 56]

In [26]:
len(id_points_align)

6

In [27]:
# prepare intermediated data in alignment_stationed_df required to interpolate alignment elevations

# fill in "Elevation" and "distance_intermed_align" for points in alignment_stationed_df 
#   where points of alignment_points_df != alignment_df

# why is this needed??                                                                                ToDo: JK
for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "Elevation"] = ( 
                                                                    alignment_df["Elevation"][n] )

for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "distance_intermed_align"] = ( 
                                                        alignment_df["distance_intermed_align"][n] )

# add "distance_intermed_stat" to alignment_stationed_df 
alignment_stationed_df["distance_intermed_stat"] = np.nan

for n in range(0, 1):
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
                                id_points_align[n +1]))), "distance_intermed_stat"] =  ( 
                                                    alignment_stationed_df["distance_stat_sum"] )
### for n in range(1, len(id_points_align) -1): 
###     alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
###                                 id_points_align[n +1]))), "distance_intermed_stat"] = ( 
###                                                     alignment_stationed_df["distance_stat_sum"] - 
###                                                     alignment_df["distance_intermed_align"][n -1] )
for n in range(1, len(id_points_align) -1):
      alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
                                  id_points_align[n +1]))), "distance_intermed_stat"] = ( 
                                             alignment_stationed_df["distance_stat_sum"] - 
                                             alignment_stationed_df["distance_stat_sum"][id_points_align[n] -1] )
    
#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   632522.964000  6.038616e+06         0      49.858322       16956.000000   
1   632473.123708  6.038617e+06         1      49.858322       17005.858322   
2   632423.283417  6.038619e+06         2      49.858322       17055.716644   
3   632373.443125  6.038620e+06         3      49.858322       17105.574966   
4   632323.602833  6.038621e+06         4      49.858322       17155.433288   
5   632273.762542  6.038623e+06         5      49.858322       17205.291611   
6   632223.922250  6.038624e+06         6      49.858322       17255.149933   
7   632174.081958  6.038625e+06         7      49.858322       17305.008255   
8   632124.241667  6.038627e+06         8      49.858322       17354.866577   
9   632074.401375  6.038628e+06         9      49.858322       17404.724899   
10  632024.561083  6.038629e+06        10      49.858322       17454.583221   
11  631974.720792  6.038631e+06        11      49.858322       17504.441543   
12  631924.880500  6.038632e+06        12      49.858322       17554.299865   
13  631875.040208  6.038633e+06        13      49.858322       17604.158187   
14  631825.199917  6.038635e+06        14      49.858322       17654.016510   
15  631775.359625  6.038636e+06        15      49.858322       17703.874832   
16  631725.519333  6.038637e+06        16      49.858322       17753.733154   
17  631675.679042  6.038639e+06        17      49.858322       17803.591476   
18  631625.838750  6.038640e+06        18      49.858322       17853.449798   
19  631575.998458  6.038641e+06        19      49.858322       17903.308120   
20  631526.158167  6.038643e+06        20      49.858322       17953.166442   
21  631476.317875  6.038644e+06        21      49.858322       18003.024764   
22  631426.477583  6.038646e+06        22      49.858322       18052.883086   
23  631376.637292  6.038647e+06        23      49.858322       18102.741409   
24  631326.797000  6.038648e+06        24      49.858322       18152.599731   
25  631276.956708  6.038650e+06        25      49.858322       18202.458053   
26  631227.116417  6.038651e+06        26      49.858322       18252.316375   
27  631177.276125  6.038652e+06        27      49.858322       18302.174697   
28  631127.435833  6.038654e+06        28      49.858322       18352.033019   
29  631077.595542  6.038655e+06        29      49.858322       18401.891341   
30  631027.755250  6.038656e+06        30      49.858322       18451.749663   
31  630977.914958  6.038658e+06        31      49.858322       18501.607986   
32  630928.074667  6.038659e+06        32      49.858322       18551.466308   
33  630878.234375  6.038660e+06        33      49.858322       18601.324630   
34  630828.394083  6.038662e+06        34      49.858322       18651.182952   
35  630778.553792  6.038663e+06        35      49.858322       18701.041274   
36  630728.713500  6.038664e+06        36      49.858322       18750.899596   
37  630678.873208  6.038666e+06        37      49.858322       18800.757918   
38  630629.032917  6.038667e+06        38      49.858322       18850.616240   
39  630579.192625  6.038668e+06        39      49.858322       18900.474562   
40  630529.352333  6.038670e+06        40      49.858322       18950.332885   
41  630479.512042  6.038671e+06        41      49.858322       19000.191207   
42  630429.671750  6.038672e+06        42      49.858322       19050.049529   
43  630379.831458  6.038674e+06        43      49.858322       19099.907851   
44  630329.991167  6.038675e+06        44      49.858322       19149.766173   
45  630280.150875  6.038676e+06        45      49.858322       19199.624495   
46  630230.310583  6.038678e+06        46      49.858322       19249.482817   
47  630180.470292  6.038679e+06        47      49.858322       19299.341139   
48  630130.630000  6.038680e+06        48      40.714660       19349.199461   
49  630089.930250  6.038681e+06        49      40.714660    

In [28]:
# interpolate alignment elevation ("z_align") at all station points and write to alignment_stationed_df

# add variable "z_align" to alignment_stationed_df
alignment_stationed_df["z_align"] = np.nan

for i in range(0, len(alignment_stationed_df)):
    ####print('i: ',i)
    # alignment points
    if i in id_points_align:
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                                                        alignment_stationed_df.iloc[i]["Elevation"] )
    # stationed points
    else:
        id_points_align_plus_point_n = id_points_align
        id_points_align_plus_point_n.append(i)
        id_points_align_plus_point_n.sort()
        m = id_points_align_plus_point_n.index(i) +1  #index of point n +1 (next alignment point)
        n = id_points_align_plus_point_n[m]  #id_point of next alignment point  
        o = id_points_align_plus_point_n.index(i) -1  #index of point n -1 (previous alignment point)
        p = id_points_align_plus_point_n[o]  #id_point of previous alignment point
            
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                                                    alignment_stationed_df.iloc[p]["Elevation"] 
                                                    +(alignment_stationed_df.iloc[n]["Elevation"] 
                                                    -alignment_stationed_df.iloc[p]["Elevation"]) 
                                                        /alignment_stationed_df.iloc[i]["distance_intermed_align"]
                                                        *alignment_stationed_df.iloc[i-1]["distance_intermed_stat"] )

        id_points_align_plus_point_n.remove(i)  #needed ??                                           #ToDo JK

alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_align"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_stat"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["Elevation"])

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   632522.964000  6.038616e+06         0      49.858322       16956.000000   
1   632473.123708  6.038617e+06         1      49.858322       17005.858322   
2   632423.283417  6.038619e+06         2      49.858322       17055.716644   
3   632373.443125  6.038620e+06         3      49.858322       17105.574966   
4   632323.602833  6.038621e+06         4      49.858322       17155.433288   
5   632273.762542  6.038623e+06         5      49.858322       17205.291611   
6   632223.922250  6.038624e+06         6      49.858322       17255.149933   
7   632174.081958  6.038625e+06         7      49.858322       17305.008255   
8   632124.241667  6.038627e+06         8      49.858322       17354.866577   
9   632074.401375  6.038628e+06         9      49.858322       17404.724899   
10  632024.561083  6.038629e+06        10      49.858322       17454.583221   
11  631974.720792  6.038631e+06        11      49.858322       17504.441543   
12  631924.880500  6.038632e+06        12      49.858322       17554.299865   
13  631875.040208  6.038633e+06        13      49.858322       17604.158187   
14  631825.199917  6.038635e+06        14      49.858322       17654.016510   
15  631775.359625  6.038636e+06        15      49.858322       17703.874832   
16  631725.519333  6.038637e+06        16      49.858322       17753.733154   
17  631675.679042  6.038639e+06        17      49.858322       17803.591476   
18  631625.838750  6.038640e+06        18      49.858322       17853.449798   
19  631575.998458  6.038641e+06        19      49.858322       17903.308120   
20  631526.158167  6.038643e+06        20      49.858322       17953.166442   
21  631476.317875  6.038644e+06        21      49.858322       18003.024764   
22  631426.477583  6.038646e+06        22      49.858322       18052.883086   
23  631376.637292  6.038647e+06        23      49.858322       18102.741409   
24  631326.797000  6.038648e+06        24      49.858322       18152.599731   
25  631276.956708  6.038650e+06        25      49.858322       18202.458053   
26  631227.116417  6.038651e+06        26      49.858322       18252.316375   
27  631177.276125  6.038652e+06        27      49.858322       18302.174697   
28  631127.435833  6.038654e+06        28      49.858322       18352.033019   
29  631077.595542  6.038655e+06        29      49.858322       18401.891341   
30  631027.755250  6.038656e+06        30      49.858322       18451.749663   
31  630977.914958  6.038658e+06        31      49.858322       18501.607986   
32  630928.074667  6.038659e+06        32      49.858322       18551.466308   
33  630878.234375  6.038660e+06        33      49.858322       18601.324630   
34  630828.394083  6.038662e+06        34      49.858322       18651.182952   
35  630778.553792  6.038663e+06        35      49.858322       18701.041274   
36  630728.713500  6.038664e+06        36      49.858322       18750.899596   
37  630678.873208  6.038666e+06        37      49.858322       18800.757918   
38  630629.032917  6.038667e+06        38      49.858322       18850.616240   
39  630579.192625  6.038668e+06        39      49.858322       18900.474562   
40  630529.352333  6.038670e+06        40      49.858322       18950.332885   
41  630479.512042  6.038671e+06        41      49.858322       19000.191207   
42  630429.671750  6.038672e+06        42      49.858322       19050.049529   
43  630379.831458  6.038674e+06        43      49.858322       19099.907851   
44  630329.991167  6.038675e+06        44      49.858322       19149.766173   
45  630280.150875  6.038676e+06        45      49.858322       19199.624495   
46  630230.310583  6.038678e+06        46      49.858322       19249.482817   
47  630180.470292  6.038679e+06        47      49.858322       19299.341139   
48  630130.630000  6.038680e+06        48      40.714660       19349.199461   
49  630089.930250  6.038681e+06        49      40.714660    

In [29]:
# add required field "z_dtm_align" to alignment_stationed_df 

# list of shapely geometry points                                                #ToDo JK: make df -> shp function           
alignment_stationed_geometry = ( 
    [sp.geometry.Point(row['x_align'], row['y_align']) for key, row in alignment_stationed_df.iterrows()] )
# create alignment_stationed_geometry_df
alignment_stationed_geometry_df = ( 
    gpd.GeoDataFrame(alignment_stationed_df, geometry=alignment_stationed_geometry, crs = crs) )
# write df to Alignment_stationed_shp (overwrite file)
alignment_stationed_geometry_df.to_file(Alignment_stationed_shp, driver='ESRI Shapefile') 

# get DTM values for alignment_points                                     #ToDo JK: make into what.points function
#   write to Alignment_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Alignment_stationed_shp, "NA",",", 500,
                  True,False,False,False,False,grass_region,-1,0.0001,Alignment_dtm_csv)

# create alignment_dtm_df (dataframe) from Alignment_dtm_csv 
alignment_dtm_df = pd.read_csv(Alignment_dtm_csv)

# rename col=tmp... to "z_dtm_align"
alignment_dtm_df_col_tmp = [col for col in alignment_dtm_df.columns if 'tmp' in col]
if len(alignment_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for alignment. Please check"
    exit()
alignment_dtm_df = alignment_dtm_df.rename(
    columns= {alignment_dtm_df_col_tmp[0]: "z_dtm_align"})

# write alignment_dtm_df["z_dtm_align"] to alignment_stationed_df["z_dtm_align"]
alignment_stationed_df["z_dtm_align"] = alignment_dtm_df["z_dtm_align"]

alignment_stationed_df = alignment_stationed_df.drop(columns = ["geometry"])

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   632522.964000  6.038616e+06         0      49.858322       16956.000000   
1   632473.123708  6.038617e+06         1      49.858322       17005.858322   
2   632423.283417  6.038619e+06         2      49.858322       17055.716644   
3   632373.443125  6.038620e+06         3      49.858322       17105.574966   
4   632323.602833  6.038621e+06         4      49.858322       17155.433288   
5   632273.762542  6.038623e+06         5      49.858322       17205.291611   
6   632223.922250  6.038624e+06         6      49.858322       17255.149933   
7   632174.081958  6.038625e+06         7      49.858322       17305.008255   
8   632124.241667  6.038627e+06         8      49.858322       17354.866577   
9   632074.401375  6.038628e+06         9      49.858322       17404.724899   
10  632024.561083  6.038629e+06        10      49.858322       17454.583221   
11  631974.720792  6.038631e+06        11      49.858322       17504.441543   
12  631924.880500  6.038632e+06        12      49.858322       17554.299865   
13  631875.040208  6.038633e+06        13      49.858322       17604.158187   
14  631825.199917  6.038635e+06        14      49.858322       17654.016510   
15  631775.359625  6.038636e+06        15      49.858322       17703.874832   
16  631725.519333  6.038637e+06        16      49.858322       17753.733154   
17  631675.679042  6.038639e+06        17      49.858322       17803.591476   
18  631625.838750  6.038640e+06        18      49.858322       17853.449798   
19  631575.998458  6.038641e+06        19      49.858322       17903.308120   
20  631526.158167  6.038643e+06        20      49.858322       17953.166442   
21  631476.317875  6.038644e+06        21      49.858322       18003.024764   
22  631426.477583  6.038646e+06        22      49.858322       18052.883086   
23  631376.637292  6.038647e+06        23      49.858322       18102.741409   
24  631326.797000  6.038648e+06        24      49.858322       18152.599731   
25  631276.956708  6.038650e+06        25      49.858322       18202.458053   
26  631227.116417  6.038651e+06        26      49.858322       18252.316375   
27  631177.276125  6.038652e+06        27      49.858322       18302.174697   
28  631127.435833  6.038654e+06        28      49.858322       18352.033019   
29  631077.595542  6.038655e+06        29      49.858322       18401.891341   
30  631027.755250  6.038656e+06        30      49.858322       18451.749663   
31  630977.914958  6.038658e+06        31      49.858322       18501.607986   
32  630928.074667  6.038659e+06        32      49.858322       18551.466308   
33  630878.234375  6.038660e+06        33      49.858322       18601.324630   
34  630828.394083  6.038662e+06        34      49.858322       18651.182952   
35  630778.553792  6.038663e+06        35      49.858322       18701.041274   
36  630728.713500  6.038664e+06        36      49.858322       18750.899596   
37  630678.873208  6.038666e+06        37      49.858322       18800.757918   
38  630629.032917  6.038667e+06        38      49.858322       18850.616240   
39  630579.192625  6.038668e+06        39      49.858322       18900.474562   
40  630529.352333  6.038670e+06        40      49.858322       18950.332885   
41  630479.512042  6.038671e+06        41      49.858322       19000.191207   
42  630429.671750  6.038672e+06        42      49.858322       19050.049529   
43  630379.831458  6.038674e+06        43      49.858322       19099.907851   
44  630329.991167  6.038675e+06        44      49.858322       19149.766173   
45  630280.150875  6.038676e+06        45      49.858322       19199.624495   
46  630230.310583  6.038678e+06        46      49.858322       19249.482817   
47  630180.470292  6.038679e+06        47      49.858322       19299.341139   
48  630130.630000  6.038680e+06        48      40.714660       19349.199461   
49  630089.930250  6.038681e+06        49      40.714660    

In [30]:
# Add require field "h" to alignment_stationed_df = overburden depth above station point 
alignment_stationed_df["h"] = alignment_stationed_df["z_dtm_align"] - alignment_stationed_df["z_align"] 

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   632522.964000  6.038616e+06         0      49.858322       16956.000000   
1   632473.123708  6.038617e+06         1      49.858322       17005.858322   
2   632423.283417  6.038619e+06         2      49.858322       17055.716644   
3   632373.443125  6.038620e+06         3      49.858322       17105.574966   
4   632323.602833  6.038621e+06         4      49.858322       17155.433288   
5   632273.762542  6.038623e+06         5      49.858322       17205.291611   
6   632223.922250  6.038624e+06         6      49.858322       17255.149933   
7   632174.081958  6.038625e+06         7      49.858322       17305.008255   
8   632124.241667  6.038627e+06         8      49.858322       17354.866577   
9   632074.401375  6.038628e+06         9      49.858322       17404.724899   
10  632024.561083  6.038629e+06        10      49.858322       17454.583221   
11  631974.720792  6.038631e+06        11      49.858322       17504.441543   
12  631924.880500  6.038632e+06        12      49.858322       17554.299865   
13  631875.040208  6.038633e+06        13      49.858322       17604.158187   
14  631825.199917  6.038635e+06        14      49.858322       17654.016510   
15  631775.359625  6.038636e+06        15      49.858322       17703.874832   
16  631725.519333  6.038637e+06        16      49.858322       17753.733154   
17  631675.679042  6.038639e+06        17      49.858322       17803.591476   
18  631625.838750  6.038640e+06        18      49.858322       17853.449798   
19  631575.998458  6.038641e+06        19      49.858322       17903.308120   
20  631526.158167  6.038643e+06        20      49.858322       17953.166442   
21  631476.317875  6.038644e+06        21      49.858322       18003.024764   
22  631426.477583  6.038646e+06        22      49.858322       18052.883086   
23  631376.637292  6.038647e+06        23      49.858322       18102.741409   
24  631326.797000  6.038648e+06        24      49.858322       18152.599731   
25  631276.956708  6.038650e+06        25      49.858322       18202.458053   
26  631227.116417  6.038651e+06        26      49.858322       18252.316375   
27  631177.276125  6.038652e+06        27      49.858322       18302.174697   
28  631127.435833  6.038654e+06        28      49.858322       18352.033019   
29  631077.595542  6.038655e+06        29      49.858322       18401.891341   
30  631027.755250  6.038656e+06        30      49.858322       18451.749663   
31  630977.914958  6.038658e+06        31      49.858322       18501.607986   
32  630928.074667  6.038659e+06        32      49.858322       18551.466308   
33  630878.234375  6.038660e+06        33      49.858322       18601.324630   
34  630828.394083  6.038662e+06        34      49.858322       18651.182952   
35  630778.553792  6.038663e+06        35      49.858322       18701.041274   
36  630728.713500  6.038664e+06        36      49.858322       18750.899596   
37  630678.873208  6.038666e+06        37      49.858322       18800.757918   
38  630629.032917  6.038667e+06        38      49.858322       18850.616240   
39  630579.192625  6.038668e+06        39      49.858322       18900.474562   
40  630529.352333  6.038670e+06        40      49.858322       18950.332885   
41  630479.512042  6.038671e+06        41      49.858322       19000.191207   
42  630429.671750  6.038672e+06        42      49.858322       19050.049529   
43  630379.831458  6.038674e+06        43      49.858322       19099.907851   
44  630329.991167  6.038675e+06        44      49.858322       19149.766173   
45  630280.150875  6.038676e+06        45      49.858322       19199.624495   
46  630230.310583  6.038678e+06        46      49.858322       19249.482817   
47  630180.470292  6.038679e+06        47      49.858322       19299.341139   
48  630130.630000  6.038680e+06        48      40.714660       19349.199461   
49  630089.930250  6.038681e+06        49      40.714660    

In [31]:
# define make_buffer to get buffer grid points at all station points along alignment
def make_buffer(point, overburden, c, res):
    h = overburden
    if h < 0.0:
        print "Overburden is negative. Please check"
        exit()
    intvls_r = max(int(h*c / res), 1)  #number of intervals along the buffer radius, close enough
    res_r = h*c / intvls_r  #effective resolution along the radius
    buffer = np.array(point)  #initialize buffer, first item is exactly at station point

    # calculate local coordinates for grid along a ring and add to point coor
    for i in range(intvls_r):
        r = c*h - i*res_r
        perim = 2 * r * pi 
        intvls_c = max(int(perim/res), 1)  #number of intervals along a ring, close enough
        item = np.array([0.0, 0.0])  #initialize       
        for j in range(intvls_c):
            item[0] = (sin((2*pi) / intvls_c *(j+1)) *r) + point[0]
            item[1] = (cos((2*pi) / intvls_c *(j+1)) *r) + point[1]
            buffer = np.vstack((buffer, item))  #vstack works with arrays of diff nr of items, append does not        

    return buffer

In [32]:
# create csv file with all buffer points     #ToDo KLK: make check plot of alignment, station points, buffer_all

# point = alignment_stationed_xy
# create alignment_stationed_xy from alignment_stationed_df with x,y of all station points
alignment_stationed_xy = alignment_stationed_df.as_matrix(columns=['x_align','y_align'])
# overburden = alignment_stationed_h
alignment_stationed_h = alignment_stationed_df.as_matrix(columns=['h'])

# initialize buffer_df, buffer_all_df, buffer_all
buffer_all = {}
buffer_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h" ,"x_buffer", "y_buffer"])
buffer_all_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h","x_buffer", "y_buffer"])

for n in range(0, len(alignment_stationed_df)):
    ####print('n: ',n)
    buffer_point = make_buffer(point=alignment_stationed_xy[n], overburden=alignment_stationed_h[n], c=c, res=res)
    buffer_all[n] = buffer_df.copy(deep=False)  #copy of initialized buffer_df
    #print("n: ", n)
    #print(buffer_all)
    buffer_all[n]["id_point"] = [n] * len(buffer_point)  #list with len(buffer_point) number of n values) 
    ####buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    ####buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["x_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("x_align")]] * len(buffer_point) )      
    buffer_all[n]["y_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("y_align")]] * len(buffer_point) )      
    buffer_all[n]["z_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("z_align")]] * len(buffer_point) )           
    buffer_all[n]["h"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("h")]] * len(buffer_point) )           
    buffer_all[n]["x_buffer"] = buffer_point[0:,0]
    buffer_all[n]["y_buffer"] = buffer_point[0:,1]
    buffer_all_df = pd.concat([buffer_all_df, buffer_all[n]])
    #print(buffer_all_df)

# add variable "id_buffer_point" to buffer_all_df
buffer_all_df = buffer_all_df.reset_index(drop=True)
buffer_all_df["id_buffer_point"] = buffer_all_df.index    

# save buffer_all_df to csv
buffer_all_df.to_csv(Buffer_all_csv, sep=",", na_rep="NaN")

buffer_all_df.head()

dist_stat      h id_point  stat_sum     x_align       x_buffer  \
0  49.858322  224.0        0   16956.0  632522.964  632522.964000   
1  49.858322  224.0        0   16956.0  632522.964  632547.886345   
2  49.858322  224.0        0   16956.0  632522.964  632571.558979   
3  49.858322  224.0        0   16956.0  632522.964  632592.794858   
4  49.858322  224.0        0   16956.0  632522.964  632610.529126   

       y_align      y_buffer  z_align  id_buffer_point  
0  6038616.024  6.038616e+06   1101.0                0  
1  6038616.024  6.038725e+06   1101.0                1  
2  6038616.024  6.038717e+06   1101.0                2  
3  6038616.024  6.038704e+06   1101.0                3  
4  6038616.024  6.038686e+06   1101.0                4

In [33]:
# add required field "z_dtm_buffer" and calcualted "dist" to buffer_all_df 
# add required field "slope" to buffer_all_df 

# buffer_all_df to Buffer_all_shp                                   #ToDo JK: reuse df -> shp function from above
# list of shapely geometry points
buffer_all_geometry = ( 
    [sp.geometry.Point(row['x_buffer'], row['y_buffer']) for key, row in buffer_all_df.iterrows()] )
# create buffer_all_geometry_df
buffer_all_geometry_df = gpd.GeoDataFrame(buffer_all_df, geometry=buffer_all_geometry, crs = crs)
# write df to Buffer_all_shp
buffer_all_geometry_df.to_file(Buffer_all_shp, driver='ESRI Shapefile') 
#print(buffer_all_geometry_df.head())

# get DTM values for Buffer_all_shp                             #ToDo JK: reuse what.points function from above
#   write to Buffer_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_dtm_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_dtm_df = pd.read_csv(Buffer_dtm_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_dtm_df_col_tmp = [col for col in buffer_dtm_df.columns if 'tmp' in col]
if len(buffer_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for buffer. Please check"
    exit()
buffer_dtm_df = buffer_dtm_df.rename(
    columns= {buffer_dtm_df_col_tmp[0]: "z_dtm_buffer"})
#print(buffer_dtm_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["z_dtm_buffer"] = buffer_dtm_df["z_dtm_buffer"]
#print(buffer_all_df.head())


# get slope values for Buffer_all_shp
#   write to Buffer_slope_csv
processing.runalg("grass7:r.what.points",DTM_slope,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_slope_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_slope_df = pd.read_csv(Buffer_slope_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_slope_df_col_tmp = [col for col in buffer_slope_df.columns if 'tmp' in col]
if len(buffer_slope_df_col_tmp) != 1:
    print "Extraction of Slope col=tmp did not work properly for buffer. Please check"
    exit()
buffer_slope_df = buffer_slope_df.rename(
    columns= {buffer_slope_df_col_tmp[0]: "slope"})
#print(buffer_slope_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["slope"] = buffer_slope_df["slope"]


# calculate "dist" between each buffer point and associated alignment point 
buffer_all_df["dist"] = (((buffer_all_df["x_align"] - buffer_all_df["x_buffer"])**2 + 
                         (buffer_all_df["y_align"] - buffer_all_df["y_buffer"]) **2) +
                         (buffer_all_df["z_dtm_buffer"] - buffer_all_df["z_align"]) **2) **(0.5)

# clean up
buffer_all_df = buffer_all_df.drop(columns =["geometry"])
buffer_all_df.head()

dist_stat      h id_point  stat_sum     x_align       x_buffer  \
0  49.858322  224.0        0   16956.0  632522.964  632522.964000   
1  49.858322  224.0        0   16956.0  632522.964  632547.886345   
2  49.858322  224.0        0   16956.0  632522.964  632571.558979   
3  49.858322  224.0        0   16956.0  632522.964  632592.794858   
4  49.858322  224.0        0   16956.0  632522.964  632610.529126   

       y_align      y_buffer  z_align  id_buffer_point  z_dtm_buffer  \
0  6038616.024  6.038616e+06   1101.0                0        1325.0   
1  6038616.024  6.038725e+06   1101.0                1        1315.0   
2  6038616.024  6.038717e+06   1101.0                2        1320.0   
3  6038616.024  6.038704e+06   1101.0                3        1330.0   
4  6038616.024  6.038686e+06   1101.0                4        1330.0   

       slope        dist  
0   9.468959  224.000000  
1  13.021960  241.536747  
2  14.771009  245.977641  
3  17.107254  254.921557  
4  17.107254  254.921557

In [34]:
buffer_all_df

dist_stat           h id_point      stat_sum        x_align  \
0     49.858322  224.000000        0  16956.000000  632522.964000   
1     49.858322  224.000000        0  16956.000000  632522.964000   
2     49.858322  224.000000        0  16956.000000  632522.964000   
3     49.858322  224.000000        0  16956.000000  632522.964000   
4     49.858322  224.000000        0  16956.000000  632522.964000   
5     49.858322  224.000000        0  16956.000000  632522.964000   
6     49.858322  224.000000        0  16956.000000  632522.964000   
7     49.858322  224.000000        0  16956.000000  632522.964000   
8     49.858322  224.000000        0  16956.000000  632522.964000   
9     49.858322  224.000000        0  16956.000000  632522.964000   
10    49.858322  224.000000        0  16956.000000  632522.964000   
11    49.858322  224.000000        0  16956.000000  632522.964000   
12    49.858322  224.000000        0  16956.000000  632522.964000   
13    49.858322  224.000000        0  16956.000000  632522.964000   
14    49.858322  224.000000        0  16956.000000  632522.964000   
15    49.858322  224.000000        0  16956.000000  632522.964000   
16    49.858322  224.000000        0  16956.000000  632522.964000   
17    49.858322  224.000000        0  16956.000000  632522.964000   
18    49.858322  224.000000        0  16956.000000  632522.964000   
19    49.858322  224.000000        0  16956.000000  632522.964000   
20    49.858322  224.000000        0  16956.000000  632522.964000   
21    49.858322  224.000000        0  16956.000000  632522.964000   
22    49.858322  224.000000        0  16956.000000  632522.964000   
23    49.858322  224.000000        0  16956.000000  632522.964000   
24    49.858322  224.000000        0  16956.000000  632522.964000   
25    49.858322  224.000000        0  16956.000000  632522.964000   
26    49.858322  224.000000        0  16956.000000  632522.964000   
27    49.858322  224.000000        0  16956.000000  632522.964000   
28    49.858322  224.000000        0  16956.000000  632522.964000   
29    49.858322  224.000000        0  16956.000000  632522.964000   
30    49.858322  224.000000        0  16956.000000  632522.964000   
31    49.858322  224.000000        0  16956.000000  632522.964000   
32    49.858322  224.000000        0  16956.000000  632522.964000   
33    49.858322  224.000000        0  16956.000000  632522.964000   
34    49.858322  224.000000        0  16956.000000  632522.964000   
35    49.858322  224.000000        0  16956.000000  632522.964000   
36    49.858322  224.000000        0  16956.000000  632522.964000   
37    49.858322  224.000000        0  16956.000000  632522.964000   
38    49.858322  224.000000        0  16956.000000  632522.964000   
39    49.858322  224.000000        0  16956.000000  632522.964000   
40    49.858322  224.000000        0  16956.000000  632522.964000   
41    49.858322  224.000000        0  16956.000000  632522.964000   
42    49.858322  224.000000        0  16956.000000  632522.964000   
43    49.858322  224.000000        0  16956.000000  632522.964000   
44    49.858322  224.000000        0  16956.000000  632522.964000   
45    49.858322  224.000000        0  16956.000000  632522.964000   
46    49.858322  224.000000        0  16956.000000  632522.964000   
47    49.858322  224.000000        0  16956.000000  632522.964000   
48    49.858322  224.000000        0  16956.000000  632522.964000   
49    49.858322  224.000000        0  16956.000000  632522.964000   
50    49.858322  224.000000        0  16956.000000  632522.964000   
51    49.858322  224.000000        0  16956.000000  632522.964000   
52    49.858322  224.000000        0  16956.000000  632522.964000   
53    49.858322  224.000000        0  16956.000000  632522.964000   
54    49.858322  224.000000        0  16956.000000  632522.964000   
55    49.858322  224.000000        0  16956.000000  632522.964000   
56    49.858322  224.000000        0  16956.000000  632522.964000   
57  

In [35]:
# calculate minimum distance to terrain in each buffer ring
                                                #ToDo KLK: make check plot of id_buffer_points with "min_dist"
                                                #ToDo JK: add station field
buffer_all_df["min_dist"] = np.nan

for n in range(0, len(alignment_stationed_df)):
    buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["id_point"] == n),]
    dist_idxmin=buffer_all_df_sel['dist'].idxmin()
    buffer_all_df.loc[(buffer_all_df["id_buffer_point"] == dist_idxmin), "min_dist"] = "MIN"

buffer_all_df.to_csv(Buffer_all_csv, header=True, index=False)  #no header
buffer_all_df

#buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]

dist_stat           h id_point      stat_sum        x_align  \
0     49.858322  224.000000        0  16956.000000  632522.964000   
1     49.858322  224.000000        0  16956.000000  632522.964000   
2     49.858322  224.000000        0  16956.000000  632522.964000   
3     49.858322  224.000000        0  16956.000000  632522.964000   
4     49.858322  224.000000        0  16956.000000  632522.964000   
5     49.858322  224.000000        0  16956.000000  632522.964000   
6     49.858322  224.000000        0  16956.000000  632522.964000   
7     49.858322  224.000000        0  16956.000000  632522.964000   
8     49.858322  224.000000        0  16956.000000  632522.964000   
9     49.858322  224.000000        0  16956.000000  632522.964000   
10    49.858322  224.000000        0  16956.000000  632522.964000   
11    49.858322  224.000000        0  16956.000000  632522.964000   
12    49.858322  224.000000        0  16956.000000  632522.964000   
13    49.858322  224.000000        0  16956.000000  632522.964000   
14    49.858322  224.000000        0  16956.000000  632522.964000   
15    49.858322  224.000000        0  16956.000000  632522.964000   
16    49.858322  224.000000        0  16956.000000  632522.964000   
17    49.858322  224.000000        0  16956.000000  632522.964000   
18    49.858322  224.000000        0  16956.000000  632522.964000   
19    49.858322  224.000000        0  16956.000000  632522.964000   
20    49.858322  224.000000        0  16956.000000  632522.964000   
21    49.858322  224.000000        0  16956.000000  632522.964000   
22    49.858322  224.000000        0  16956.000000  632522.964000   
23    49.858322  224.000000        0  16956.000000  632522.964000   
24    49.858322  224.000000        0  16956.000000  632522.964000   
25    49.858322  224.000000        0  16956.000000  632522.964000   
26    49.858322  224.000000        0  16956.000000  632522.964000   
27    49.858322  224.000000        0  16956.000000  632522.964000   
28    49.858322  224.000000        0  16956.000000  632522.964000   
29    49.858322  224.000000        0  16956.000000  632522.964000   
30    49.858322  224.000000        0  16956.000000  632522.964000   
31    49.858322  224.000000        0  16956.000000  632522.964000   
32    49.858322  224.000000        0  16956.000000  632522.964000   
33    49.858322  224.000000        0  16956.000000  632522.964000   
34    49.858322  224.000000        0  16956.000000  632522.964000   
35    49.858322  224.000000        0  16956.000000  632522.964000   
36    49.858322  224.000000        0  16956.000000  632522.964000   
37    49.858322  224.000000        0  16956.000000  632522.964000   
38    49.858322  224.000000        0  16956.000000  632522.964000   
39    49.858322  224.000000        0  16956.000000  632522.964000   
40    49.858322  224.000000        0  16956.000000  632522.964000   
41    49.858322  224.000000        0  16956.000000  632522.964000   
42    49.858322  224.000000        0  16956.000000  632522.964000   
43    49.858322  224.000000        0  16956.000000  632522.964000   
44    49.858322  224.000000        0  16956.000000  632522.964000   
45    49.858322  224.000000        0  16956.000000  632522.964000   
46    49.858322  224.000000        0  16956.000000  632522.964000   
47    49.858322  224.000000        0  16956.000000  632522.964000   
48    49.858322  224.000000        0  16956.000000  632522.964000   
49    49.858322  224.000000        0  16956.000000  632522.964000   
50    49.858322  224.000000        0  16956.000000  632522.964000   
51    49.858322  224.000000        0  16956.000000  632522.964000   
52    49.858322  224.000000        0  16956.000000  632522.964000   
53    49.858322  224.000000        0  16956.000000  632522.964000   
54    49.858322  224.000000        0  16956.000000  632522.964000   
55    49.858322  224.000000        0  16956.000000  632522.964000   
56    49.858322  224.000000        0  16956.000000  632522.964000   
57  

In [36]:
# calculate hydraulic confinement safety factor at each station point
#   required input data: reference maximum water pressure elevation (static or dynamic ??) 


buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]


dist = array(buffer_all_df_sel['dist'])
slope = array(buffer_all_df_sel['slope'])
z_align = array(buffer_all_df_sel['z_align'])
stat_sum = array(buffer_all_df_sel['stat_sum'])
stat_sum[0] = 0  #correction for station_stat_sum being for n-1 above (to be fixed above)

FS = (dist * 28.0 * cos(slope*pi/180.)) / ((max_static_water_level - z_align) * 10)
print(FS)
print(stat_sum)

buffer_all_df_sel["FS"] = np.nan
for n in range(0, len(buffer_all_df_sel)):
    buffer_all_df_sel.iloc[n, buffer_all_df_sel.columns.get_loc("FS")] = FS[n]

buffer_all_df_sel = buffer_all_df_sel.drop(columns =["x_align", "y_align", "min_dist", "id_buffer_point"])
    

[2.8769281  2.85265841 2.83109437 2.89973369 2.73018644 2.57319159
 2.50796205 2.32957367 2.30886401 2.27167983 2.1937173  2.06533535
 1.97128299 1.9130471  1.82291663 1.73920182 1.76200116 1.76593202
 1.67292452 1.67329023 1.61862674 1.58481542 1.51620433 1.52474399
 1.5210315  1.48671032 1.45325841 1.41070339 1.33434201 1.29328853
 1.14338623 1.08641882 1.12147188 1.16419418 1.12680529 1.13395368
 1.15740248 1.28286935 1.37765177 1.47607436 1.45693235 1.377991
 1.34063147 1.22563062 1.13109742 1.04160057 0.95560448 0.84005621
 0.49766749 0.34376888 0.33325528 0.29897045 0.18895627 1.99029686
 1.97027197 1.92335754 1.79110303]
[    0.         17005.85832211 17055.71664423 17105.57496634
 17155.43328845 17205.29161057 17255.14993268 17305.0082548
 17354.86657691 17404.72489902 17454.58322114 17504.44154325
 17554.29986536 17604.15818748 17654.01650959 17703.8748317
 17753.73315382 17803.59147593 17853.44979804 17903.30812016
 17953.16644227 18003.02476439 18052.8830865  18102.74140861


In [37]:
#buffer_all_df_sel["stat_sum"]
#buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("stat_sum")]
buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("FS")]


2.852658406517046

In [38]:
buffer_all_df_sel

dist_stat           h id_point      stat_sum       x_buffer  \
63    49.858322  224.000000        0  16956.000000  632522.964000   
127   49.858322  247.060248        1  17005.858322  632519.024095   
203   49.858322  246.411954        2  17055.716644  632469.063359   
296   49.858322  243.872332        3  17105.574966  632343.723382   
359   49.858322  238.087542        4  17155.433288  632277.066749   
416   49.858322  224.017748        5  17205.291611  632189.990786   
486   49.858322  219.090457        6  17255.149933  632145.784473   
571   49.858322  204.163165        7  17305.008255  632151.980647   
573   49.858322  194.235873        8  17354.866577  632124.241667   
668   49.858322  194.308582        9  17404.724899  632042.016611   
708   49.858322  189.381290       10  17454.583221  631998.884980   
750   49.858322  179.453998       11  17504.441543  631915.230481   
803   49.858322  174.526707       12  17554.299865  631902.138754   
844   49.858322  164.599415       13  17604.158187  631875.040208   
875   49.858322  158.814626       14  17654.016510  631781.632625   
921   49.858322  154.744832       15  17703.874832  631775.359625   
922   49.858322  148.150873       16  17753.733154  631725.519333   
977   49.858322  149.890248       17  17803.591476  631675.679042   
1008  49.858322  154.962957       18  17853.449798  631600.011591   
1036  49.858322  155.035665       19  17903.308120  631601.837736   
1080  49.858322  145.108373       20  17953.166442  631502.839701   
1106  49.858322  140.181082       21  18003.024764  631451.537127   
1131  49.858322  131.920457       22  18052.883086  631403.157121   
1133  49.858322  127.826498       23  18102.741409  631376.637292   
1158  49.858322  127.399207       24  18152.599731  631326.797000   
1205  49.858322  125.471915       25  18202.458053  631276.956708   
1206  49.858322  122.211290       26  18252.316375  631227.116417   
1248  49.858322  120.617332       27  18302.174697  631164.192650   
1252  49.858322  112.356707       28  18352.033019  631127.435833   
1285  49.858322  110.762748       29  18401.891341  631032.017564   
1312  49.858322  105.835457       30  18451.749663  631004.841201   
1314  49.858322   91.765663       31  18501.607986  630977.914958   
1326  49.858322   95.980873       32  18551.466308  630928.074667   
1347  49.858322   99.386915       33  18601.324630  630835.198578   
1358  49.858322   96.126290       34  18651.182952  630828.394083   
1365  49.858322   96.198998       35  18701.041274  630778.553792   
1392  49.858322  101.271707       36  18750.899596  630750.639468   
1411  49.858322  111.344415       37  18800.757918  630702.979981   
1435  49.858322  121.417123       38  18850.616240  630642.203146   
1458  49.858322  126.489832       39  18900.474562  630592.913095   
1463  49.858322  123.229207       40  18950.332885  630529.352333   
1486  49.858322  116.635248       41  19000.191207  630479.512042   
1508  49.858322  113.374623       42  19050.049529  630429.671750   
1547  49.858322  106.780665       43  19099.907851  630356.712766   
1550  49.858322   96.853373       44  19149.766173  630329.991167   
1572  49.858322   91.926082       45  19199.624495  630238.341422   
1575  49.858322   81.998790       46  19249.482817  630230.310583   
1593  49.858322   72.071498       47  19299.341139  630144.982006   
1600  40.714660   42.490000       48  19349.199461  630110.424804   
1602  40.714660   27.507713       49  19389.914121  630089.930250   
1606  40.714660   26.605213       50  19430.628781  630049.230500   
1612  40.714660   25.702713       51  19471.343440  629997.401149   
1614   1.000000   15.546667       52  19512.058100  629967.831000   
1942  44.700164  647.726667       53  19513.058100  629759.992549   
2587  44.700164  644.493333       54  19557.758264  629791.662401   
2992   6.220242  650.000000       55  19602.458428  629665.089251   
3440        NaN  658.000000       56  19608.678670  629613.449009   

   

In [39]:
z_dtm_align = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_dtm_align'].tolist(),
    name = "Terrain",
    mode='lines',
    line=dict(width=0.5,
              color='rgb(196, 97, 26)'),
    fill='tonexty'
)
####print('z_dtm_align',z_dtm_align)

z_align_line = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="Tunnel"
)

data = [z_dtm_align, z_align_line]

layout = go.Layout(
    title='Longitudinal Section',
    showlegend=False,
    xaxis=dict(
        title= "Stationing",
    ),
    yaxis=dict(
        title = "m a.s.l.",
        #range = [300,800]  #need a procedure to automate this
    ),
    margin=dict(
        #l=50,
        b=40
    ),
    height=400,
)

fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')



# initialize variables 
x_data = []
y_data = []
traces = []
annotations = []

fs = buffer_all_df_sel['FS'].tolist(),
c_fs = []
for i in range(len(buffer_all_df_sel.index)):
    if fs[0][i] <= 1.4:
        c_fs.append('red')
    elif 1.4 < fs[0][i] < 1.8:
        c_fs.append('yellow')
    else:
        c_fs.append('green')
slope = buffer_all_df_sel['slope'].tolist(),
c_slope = []
for i in range(len(buffer_all_df_sel.index)):
    if slope[0][i] > 30:
        c_slope.append('red')
    else:
        c_slope.append('green')        

x_data = [buffer_all_df_sel['dist_stat'].tolist()]
# x_data = [buffer_all_df_sel['dist_stat'].tolist(),
#           buffer_all_df_sel['dist_stat'].tolist()]

y_data = ['hydraulic confinement']
# y_data = ['slope',
#           'hydraulic confinement']

for i in range(0, len(x_data[0])):
    for xd, yd in zip(x_data, y_data):
        traces.append(go.Bar(
            x=[xd[i]],
            y=[yd],
            width = 0.3,
            orientation='h',
            marker=dict(
                color = c_fs[i],
            ),
            hoverinfo = 'none',
        ))
        
layout = go.Layout(
    xaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
        domain=[0.08, 1]  #horizontal extent of bar
    ),
    yaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
    ),
    barmode='stack',
    #paper_bgcolor='rgb(248, 248, 255)',
    #plot_bgcolor='rgb(248, 248, 255)',
    margin=dict(
        l=0,
        r=0,
        t=0,
        b=0
    ),
    showlegend=False,
    width=945,
    height=70,
)

for yd, xd in zip(y_data, x_data):
    # labeling the y-axis
    annotations.append(dict(xref='paper', yref='y',
                            x=0.09, y=yd, #x is position of text
                            xanchor='left',
                            text=str(yd),
                            font=dict(family='Arial', size=14,
                                      #color='rgb(67, 67, 67)'),
                                      color='white'),
                            showarrow=False, align='left'))
layout['annotations'] = annotations

fig = go.Figure(data=traces, layout=layout)
plotly.offline.iplot(fig, show_link=False, config=dict(displayModeBar=False), filename='bar-colorscale')

In [40]:
alignment_stationed_line_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="alignment_stationed_line"
)

alignment_point_plot = go.Scatter(
    x=alignment_df['Easting'].tolist(),
    y=alignment_df['Northing'].tolist(),
    name ="alignment_point",
    mode = "markers",
    marker = dict(
        size = 20,
        color = 'rgb(255, 153, 153)'
    )
)

alignment_stationed_point_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    mode = "markers",
    name ="alignment_stationed_point",
    marker = dict(
        size = 6,
        color = 'rgb(255, 0, 0)'
    )
)

buffer_all_df_point_plot = go.Scatter(
    x=buffer_all_df['x_buffer'].tolist(),
    y=buffer_all_df['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_all_point",
     marker = dict(
        size = 6,
        color = 'rgba(0, 0, 153, 0.005)'  #use for high resolution
        #color = 'rgba(0, 0, 153, 0.4)'  #use for low resolution
    )
)
buffer_min_df_point_plot = go.Scatter(
    x=buffer_all_df_sel['x_buffer'].tolist(),
    y=buffer_all_df_sel['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_min",
     marker = dict(
        size = 8,
        color = 'rgb(0, 0, 153)'
    )
)

data = [alignment_stationed_line_plot, alignment_point_plot, alignment_stationed_point_plot, 
        buffer_all_df_point_plot, buffer_min_df_point_plot]


fig = go.Figure(data=data)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')

ToDo: check that grid width is adequate (display grid points on graphic very light)
ToDo: overlay project layout as basemap (opague)

In [41]:
alignment_df.head()

Station     Northing     Easting  Elevation  distance_intermed_align
0  16956.0  6038616.024  632522.964    1101.00              2393.199461
1  19348.7  6038680.380  630130.630    1097.51               162.858638
2  19512.6  6038684.787  629967.831    1081.12                 1.000000
3  19512.6  6038684.787  629966.831     448.94                89.400328
4  19602.0  6038687.191  629877.463     440.00                 6.220242